In [22]:
import os
if "/content" in os.getcwd():
  !rm -rf WHere_codes/
  !git clone https://github.com/keenranger/WHere_codes
  os.chdir("/content/WHere_codes")
  !pip install -r requirements.txt
from PDR.modules.DataLoader import *
from PDR.modules.Walker import *

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
import plotly.graph_objects as go

In [23]:
file_name = "pt2"
pvloader = DataLoader("data/200701.db", file_name)
pvloader.loader()
sensor_df = pvloader.sensor_df[["time", "accx", "accy", "accz", "gyrox", "gyroy",
                                "gyroz", "magx", "magy", "magz","rot0", "rot1", "rot2", "rot3", "game0", "game1", "game2", "game3"]]
sensor_df.head()

Data parsing... 
Data parsing done!


time      accx      accy      accz     gyrox     gyroy     gyroz  \
0  1593662939846 -0.050276  3.926322  9.935510 -0.187970  0.134001  0.048090   
1  1593662939866 -0.119705  3.758735  9.066452 -0.011430 -0.244125  0.002275   
2  1593662939886 -0.074217  3.682124  8.894077 -0.040751 -0.116454  0.023044   
3  1593662939906  0.280110  3.797040  9.377685 -0.059077  0.070471  0.028542   
4  1593662939926  0.107734  3.830558  9.176580 -0.006543 -0.038263  0.023655   

        magx       magy       magz      rot0      rot1      rot2      rot3  \
0  25.725889 -15.816009 -40.996147  0.144214  0.142260  0.682037  0.702702   
1  24.812778 -16.396778 -41.340248  0.142732  0.141235  0.682833  0.702438   
2  25.583061 -16.100033 -41.623917  0.144208  0.139386  0.682476  0.702853   
3  24.630573 -16.272293 -39.648895  0.144349  0.138404  0.682683  0.702817   
4  24.805534 -16.111210 -40.868217  0.143550  0.138116  0.683502  0.702241   

      game0     game1     game2     game3  
0  0.201127  0.018081  0.077447  0.976331  
1  0.199937  0.017261  0.078136  0.976536  
2  0.199837  0.014678  0.077452  0.976653  
3  0.198988  0.014639  0.077550  0.976819  
4  0.198516  0.014525  0.078022  0.976879

In [24]:
walker = Walker()
for row in tqdm(sensor_df.itertuples(), total=len(sensor_df)):
    walker.step(row[0], row[1], row[2:5], row[5:8], row[8:11], row[11:15], row[15:19])


100%|██████████| 10021/10021 [00:16<00:00, 606.23it/s]


In [25]:

displacement_df = pdr_to_displacement(walker.pdr_df)
position_df = displacement_df.cumsum()
walker.pdr_df

length      body       nav       rot      game    fusion
0      0.65  1.428505  1.428505  1.428505  1.428505  1.428505
1      0.65  1.444540  1.444540  1.444540  1.444540  1.444540
2      0.65  1.454486  1.454486  1.454486  1.454486  1.454486
3      0.65  1.468260  1.468260  1.468260  1.468260  1.468260
4      0.65  1.474792  1.475561  1.474888  1.474502  1.474502
..      ...       ...       ...       ...       ...       ...
367    0.65  1.347842  1.967883  2.884870  2.946420  2.665858
368    0.65  1.346186  1.962104  2.859006  2.942508  2.661946
369    0.65  1.357053  1.970913  2.848117  2.953598  2.673036
370    0.65  1.349812  1.963548  2.831633  2.944263  2.663701
371    0.65  1.333395  1.946397  2.830224  2.924818  2.644255

[372 rows x 6 columns]

In [26]:
fig = go.Figure()
fig.add_trace(go.Scatter(
    x=position_df['rot_x'], 
    y=position_df['rot_y'],
    name="rot"))
fig.add_trace(go.Scatter(
    x=position_df['game_x'], 
    y=position_df['game_y'],
    name="game"))
fig.add_trace(go.Scatter(
    x=position_df['fusion_x'], 
    y=position_df['fusion_y'],
    name="fusion"))
fig.update_layout(
    title="PDR",
    width = 800,
    height = 800,
    yaxis = dict(
      scaleanchor = "x",
      scaleratio = 1,
    )
)
fig.show()

In [27]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=walker.headingcalc.heading_df['time'], y=np.rad2deg(walker.headingcalc.heading_df['rot']),name="rot"))
fig.add_trace(go.Scatter(x=walker.headingcalc.heading_df['time'], y=np.rad2deg(walker.headingcalc.heading_df['game']),name="game"))
fig.add_trace(go.Scatter(x=walker.headingcalc.heading_df['time'], y=np.rad2deg(walker.headingcalc.heading_df['fusion']),name="fusion"))
fig.update_layout(
    width = 800,
    height = 500
)
fig.show()

In [28]:
fig = go.Figure()
mag_df = pvloader.sensor_df[['time','magx', 'magy', 'magz']]
mag_norm = np.sqrt(mag_df['magx']**2 + mag_df['magy']**2 + mag_df['magz']**2)
fig.add_trace(go.Scatter(x=mag_df['time'], y=mag_norm, name="mag norm"))
fig.add_trace(go.Scatter(x=mag_df['time'], y=mag_norm, name="mag norm"))
fig.update_layout(
    width = 800,
    height = 500
)
fig.show()